<p>feature selection for Golestan Cohort Study:v1<br />most important and least biased features for:</p>
<ul>
<li>esophagus and stomach cancers</li>
<li>Age between 50-70</li>
<li>cross dataset "Normal"s bias analysis</li>
</ul>

# Modules and Data loading

In [1]:
import sys
import json

with open('../paths', 'r') as f:
    globals().update(json.loads(f.read()))

sys.path.append(path_Modules_Product_)
sys.path.append(path_Modules_Toolbox_)

In [2]:
import itertools
import pandas as pd
import numpy as np
from scipy import stats as scstats
from sklearn import metrics as skmet
from sklearn import preprocessing as skprep
from sklearn import covariance as skcov
from sklearn.decomposition import PCA as skpca
import matplotlib.pyplot as plt
import plotly.express as px
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

In [3]:
import Plots as IcePlot

In [4]:
dataset_base = pd.read_csv(path_data_proprocessed_ + 'dataset/ds_main.csv',
                           index_col=0)
dataset_base = dataset_base.loc[(dataset_base.s_Age.between(50, 70)) & (dataset_base.s_Sex=='M')]
# dataset_base = dataset_base.loc[(dataset_base.s_Age.between(50, 70))]

In [5]:
dataset_bias_1 = pd.read_csv(path_data_proprocessed_ + 'dataset/ds_OOB_A.csv',
                             index_col=0)
dataset_bias_1 = dataset_bias_1.loc[np.isin(dataset_bias_1.s_Group,
                                            ['Normal', 'Cancer'])]
dataset_bias_1 = dataset_bias_1.loc[dataset_bias_1.s_Age.between(50, 70)]

potential markers

In [6]:
p1 = [x for x in dataset_base.columns if x.startswith('p_')]
p2 = [x for x in dataset_bias_1.columns if x.startswith('p_')]
markers = np.array(p1)[np.isin(p1, p2)]
print(markers)

['p_CA125' 'p_CA19-9' 'p_CEA' 'p_GALECTIN3' 'p_HE4' 'p_NSE' 'p_OPG'
 'p_OPN' 'p_PROLACTIN' 'p_SHBG' 'p_TIMP1' 'p_TIMP2']


In [7]:
# test
markers = [
    'p_CA125', 'p_CA19-9', 'p_CEA', 'p_HE4', 'p_NSE', 'p_OPN', 'p_PROLACTIN',
    'p_TIMP1', 'p_TIMP2', 'p_IL6', 'p_IL8', 'p_AFP','p_CA15-3'
]

In [8]:
markers_l = [f'l_{x[2:]}-limit' for x in markers]
p_rows2 = int(np.ceil(len(markers) / 2))

# Phenotype corr.

## Sex

In [9]:
_, subs = plt.subplots(p_rows2, 2, figsize=(15, 5 * p_rows2))
subs = subs.flatten()
for c, m in enumerate(markers):
    ds = dataset_base[['s_Sex', m]].dropna()
    ds[m] = np.log(ds[m])
    ax = subs[c]
    plt.sca(ax)
    ds.groupby('s_Sex').apply(lambda x: IcePlot.linespace_kde(
        x, m, label=f'{x["s_Sex"].iloc[0]}:{len(x)}'))
    dists = []
    for _, ds_ in ds.groupby('s_Sex'):
        dists.append(ds_[m].values)
    ks = scstats.ks_2samp(*dists)
    txt = ''
    txt += 'ks:\n'
    txt += 'stat: {:.3f}\n'.format(ks.statistic)
    txt += 'pval: {:.3f}\n'.format(ks.pvalue)
    plt.text(0,
             1,
             txt,
             horizontalalignment='left',
             verticalalignment='top',
             transform=ax.transAxes)
    plt.title(m)
    plt.legend()
    plt.grid()

TypeError: ks_2samp() missing 1 required positional argument: 'data2'

## Age

In [ ]:
#

# Case vs. Control

## Dist.

In [10]:
tumor_g = ['Normal', 'Esophagus', 'Stomach']
_, subs = plt.subplots(p_rows2, 2, figsize=(15, 5 * p_rows2))
subs = subs.flatten()
ds = dataset_base.loc[np.isin(dataset_base.s_Tumor, tumor_g)].copy()
for c, m in enumerate(markers):
    ds_ = ds[['s_Tumor', m]].dropna()
    ds_[m] = np.log(ds_[m])
    ax = subs[c]
    plt.sca(ax)
    ds_.groupby('s_Tumor', sort=False).apply(lambda x: IcePlot.linespace_kde(
        x, m, label=f'{x["s_Tumor"].iloc[0]}:{len(x)}'))
    plt.title(m)
    plt.legend()
    plt.grid()

## KS

In [11]:
tumor_g = ['Normal', 'Stomach', 'Esophagus']
tmp = pd.MultiIndex.from_product((['Stomach', 'Esophagus'], ['ks', 'p']))
rep = pd.DataFrame(index=markers+['s_Age'], columns=tmp)
ds = dataset_base.loc[np.isin(dataset_base.s_Tumor, tumor_g)].copy()
for m in markers+['s_Age']:
    ds_ = ds[['s_Tumor', m]].dropna()
    ds_[m] = np.log(ds_[m])
    tmp = ds_.loc[ds_.s_Tumor == 'Normal', [m]].values
    trans = skprep.StandardScaler().fit(tmp)
    ds_[m] = trans.transform(ds_[[m]].values)
    for t in ['Stomach', 'Esophagus']:
        sam_n = ds_.loc[ds_.s_Tumor == 'Normal', m]
        sam_f = ds_.loc[ds_.s_Tumor == t, m]
        ks = scstats.ks_2samp(sam_n, sam_f)
        rep.loc[m, t] = (ks.statistic, ks.pvalue)

_, subs = plt.subplots(2, 1, figsize=(15, 8))
for c, t in enumerate(['Stomach', 'Esophagus']):
    r_ = rep[t]
    ax = subs[c]
    plt.sca(ax)
    r_ = r_.sort_values('ks')
    plt.bar(r_.index, r_.ks, label='ks-statistic')
    plt.title(t)
    plt.grid()
    plt.xticks(rotation=30)
    plt.yticks(np.arange(0, 1, 0.1))
    plt.legend(loc='upper left')
    ax = plt.twinx(ax)
    plt.plot(r_.index, r_.p, color='r', label='p_value')
    plt.yscale('log')
    plt.legend(loc='upper right')

plt.tight_layout()

## AUC

In [9]:
tumor_g = ['Normal', 'Stomach', 'Esophagus']
rep = pd.DataFrame(index=markers, columns=['Stomach', 'Esophagus'])
ds = dataset_base.copy()
for m in markers+['s_Age']:
    ds_ = ds[['s_Tumor', m]].dropna()
    ds_[m] = np.log(ds_[m])
    for t in ['Stomach', 'Esophagus']:
        ds__ = ds_.loc[np.isin(ds_.s_Tumor, ['Normal', t])].copy()
        ds__['label'] = 0
        ds__.loc[ds__.s_Tumor == t, 'label'] = 1
        auc=skmet.roc_auc_score(ds__.label,ds__[m],)
#         if auc<0.5:
#             auc=1-auc
        rep.loc[m,t]=auc
_, subs = plt.subplots(2, 1, figsize=(15, 8))
for c, t in enumerate(['Stomach', 'Esophagus']):
    r_ = rep[t]
    ax = subs[c]
    plt.sca(ax)
    r_ = r_.sort_values()
    plt.bar(r_.index, r_.values, label='ks-statistic')
    plt.title(t)
    plt.grid()
    plt.xticks(rotation=30)
    plt.yticks(np.arange(0, 1.1, 0.1))
    plt.ylim(0,1)
    plt.hlines(0.5,0,13,color='r')
plt.tight_layout()

## Median-reg

In [13]:
tumor_g = ['Normal', 'Stomach', 'Esophagus']
_, subs = plt.subplots(len(markers)+1,
                       2,
                       figsize=(15, 3 * len(markers)),
                       sharey=True)
ds = dataset_base.loc[np.isin(dataset_base.s_Tumor, tumor_g)].copy()
for c1, m in enumerate(markers+['s_Age']):
    ds_ = ds[['s_Stage', 's_Tumor', m]].dropna()
    ds_[m] = np.log(ds_[m])
    tmp = ds_.loc[ds_.s_Stage == 0, [m]].values
    trans = skprep.StandardScaler().fit(tmp)
    ds_[m] = trans.transform(ds_[[m]].values)
    for c2, t in enumerate(['Stomach', 'Esophagus']):
        ax = subs[c1, c2]
        plt.sca(ax)
        ds__ = ds_.loc[np.isin(ds_.s_Tumor, ['Normal', t]), [m, 's_Stage']]

        # -----------
        tmp = ds__.groupby('s_Stage').median()
        tmp.index += 1
        tmp.plot(ax=ax)
        # -----------
        line = scstats.linregress(ds__['s_Stage'], ds__[m])
        line_ = lambda x: x * line.slope + line.intercept
        x = np.arange(4)
        y = line_(x)
        x += 1
        plt.plot(x, y)
        txt = ''
        txt += 'intercept:{:.2f}\n'.format(line.intercept)
        txt += 'slope:{:.2f}\n'.format(line.slope)
        txt += 'rvalue:{:.2f}\n'.format(line.rvalue)
        txt += 'pvalue:{:.2f}\n'.format(line.pvalue)
        txt += 'stderr:{:.2f}\n'.format(line.stderr)
        plt.text(0,
                 1,
                 txt,
                 horizontalalignment='left',
                 verticalalignment='top',
                 transform=ax.transAxes)
        # -----------
        ds__.boxplot(m, 's_Stage', ax=ax)
        # -----------
        if c1 == 0:
            plt.title(t)
        else:
            plt.title('')
        if c1 == len(markers) - 1:
            plt.xlabel('Stage')
        else:
            plt.xlabel('')
        if c2 == 0:
            plt.ylabel(m)
#         plt.grid()
        plt.xticks([1, 2, 3, 4], [0, 1, 2, 3])
        plt.legend(['median', 'fit_line'], loc='upper right')
plt.suptitle('')
pass

## Cov.

In [14]:
tumor_g = ['Normal', 'Stomach', 'Esophagus']
ds = dataset_base.loc[np.isin(dataset_base.s_Tumor, tumor_g)].copy()
ds[markers] = np.log(ds[markers])
for t in tumor_g:
    ds_ = ds.loc[ds.s_Tumor == t].copy()
    ds_[markers] = skprep.StandardScaler().fit_transform(ds_[markers])
    corr = ds_[markers].corr('spearman')
    corr['mean'] = np.abs(corr).mean()
    corr.loc['var'] = corr.var()
    corr.iloc[-1,-1] = 0
    corr = IcePlot.corr_matrix(corr)
    print(t)
    display(corr)
    print('-' * 100)

Normal


----------------------------------------------------------------------------------------------------
Stomach


----------------------------------------------------------------------------------------------------
Esophagus


----------------------------------------------------------------------------------------------------


In [15]:
tumor_g = ['Normal', 'Stomach', 'Esophagus']
ds = dataset_base.loc[np.isin(dataset_base.s_Tumor, tumor_g)].copy()
ds[markers] = np.log(ds[markers])
ds_ = ds.loc[ds.s_Tumor == 'Normal'].copy()
ds_[markers] = skprep.StandardScaler().fit_transform(ds_[markers])
cor_norm = ds_[markers].corr()
for t in ['Stomach', 'Esophagus']:
    ds_ = ds.loc[ds.s_Tumor == t].copy()
    ds_[markers] = skprep.StandardScaler().fit_transform(ds_[markers])
    corr = ds_[markers].corr('spearman')
    corr += cor_norm
    corr /= 2
    corr['mean'] = np.abs(corr).mean()
    corr.loc['var'] = corr.var()
    corr.iloc[-1,-1] = 0
    corr = IcePlot.corr_matrix(corr)
    print(t, '+ Normal')
    display(corr)
    print('-' * 100)

Stomach + Normal


----------------------------------------------------------------------------------------------------
Esophagus + Normal


----------------------------------------------------------------------------------------------------


In [16]:
tumor_g = ['Normal', 'Stomach', 'Esophagus']
ds = dataset_base.loc[np.isin(dataset_base.s_Tumor, tumor_g)].copy()
ds[markers] = np.log(ds[markers])
corr=None
for t in tumor_g:
    ds_ = ds.loc[ds.s_Tumor == t].copy()
    ds_[markers] = skprep.StandardScaler().fit_transform(ds_[markers])
    corr_ = ds_[markers].corr('spearman')
    if corr is None:
        corr = corr_
    else:
        corr+=corr_
        
corr/=len(tumor_g)
corr['mean'] = np.abs(corr).mean()
corr.loc['var'] = corr.var()
corr.iloc[-1,-1] = 0
corr = IcePlot.corr_matrix(corr)
display(corr)

## PCA

In [17]:
tumor_g = ['Normal', 'Stomach', 'Esophagus']
ds = dataset_base.loc[np.isin(dataset_base.s_Tumor, tumor_g)].copy()
markers_=['p_IL6','p_OPN']
markers_=markers
ds[markers_] = np.log(ds[markers_])
p_=skpca(2).fit(ds[markers_])
d_=p_.transform(ds[markers_])
d_=pd.DataFrame(d_,columns=['pcax','pcay'])
d_['tumor']=ds.s_Tumor.values
px.scatter(d_,'pcax','pcay',color='tumor')